In [101]:
# Import the standard tools for working with Pandas dataframe
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import shelve

In [102]:
# Read in the file containing all the patient data
patientdata = pd.read_csv("G:/MIMIC-ALL/MIMIC-PATIENTS/patient_data.csv")


In [158]:
# Iterate over each row, calculating qSOFA and a flag if the person has Sepsis

# A function to determine a patient's qSOFA score (0-3)
def evaluateQSOFA(row):
    qSOFAScore = 0
    if row['RR'] >= 22:
        qSOFAScore = qSOFAScore + 1
    if row['GCS'] < 15:
        qSOFAScore = qSOFAScore + 1
    if row['SysBP'] <= 100:
        qSOFAScore = qSOFAScore + 1
    return qSOFAScore

# A function to flag sepsis given a patient's qSOFA score (0 or 1)
def flagQSOFA(row):
    # qSOFA of 2 or above is dangerous
    qSOFAScore = row['qSOFA']
    if(qSOFAScore >= 2):
        return 1
    return 0

# A function to flag sepsis based on a change of more than 2 points
def flagSOFA(row):
    SOFAScore = row['SOFA']
    # A single ICU visit
    icu_id = row['icustayid']
    # An ICU visit is busted up into 4hr blocs
    blocValue = row['bloc']
    # We need a change to flag Sepsis
    print(icu_id, blocValue)
    if blocValue == 1:
        return 0
    # Determine the first chart values taken
    firstEvent = patientdata.loc[(patientdata['icustayid'] == icu_id) & (patientdata['bloc'] == 1)]
    firstSOFAScore = firstEvent['SOFA'].iloc[0]
    # Determine if the SOFA score has changed by more than 2 points
    SOFAChange = row['SOFA'] - firstSOFAScore
    # If the change is more than 2 points in SOFA, we can deem that
    # there is a likelihood of Sepsis
    if SOFAChange > 2:
        return 1
    return 0

def sepsisFound(framedata, option):
    flag = ""
    if option == "qSOFAFlag":
        flag = "qSOFAFlag"
    else: 
        flag = "SOFAFlag"
    for i,  row in framedata.iterrows():
        if row[flag] == 0:
            # A single ICU visit
            icu_id = row['icustayid']
            # An ICU visit is busted up into 4hr blocs
            blocValue = row['bloc']
            if blocValue == 1:
                continue
            # Check if the previous bloc value is flagged for Sepsis
            previousEvent = framedata.loc[(patientdata['icustayid'] == icu_id) & (patientdata['bloc'] == blocValue - 1)]
            # There are some jumps in blocs due to missing rows of information
            while previousEvent[flag].empty:
                blocValue = blocValue - 1
                previousEvent = framedata.loc[(patientdata['icustayid'] == icu_id) & (patientdata['bloc'] == blocValue - 1)]
            if previousEvent[flag].iloc[0] == 1:
                framedata.loc[i, flag] = 1
                continue
            continue
        continue
    print("Finished")
    return framedata

In [148]:
# Generate the conditional columns with their diagnostic flags
patientdata['qSOFA'] = patientdata.apply(evaluateQSOFA, axis=1)

In [105]:
# Add zeroes to prevent error
patientdata['qSOFAFlag'] = 0

In [159]:
# Flag Sepsis based on qSOFA 
patientdata['qSOFAFlag'] = patientdata.apply(flagQSOFA, axis=1)

In [107]:
# Add zeroes to prevent error
patientdata['SOFAFlag'] = 0

In [131]:
# Flag Sepsis based on SOFA
patientdata['SOFAFlag'] = patientdata.apply(flagSOFA, axis=1)

3.0 1.0
3.0 2.0
3.0 3.0
3.0 4.0
3.0 5.0
3.0 6.0
3.0 7.0
3.0 8.0
3.0 9.0
3.0 10.0
3.0 11.0
3.0 12.0
3.0 15.0
11.0 1.0
11.0 2.0
11.0 3.0
11.0 4.0
11.0 5.0
11.0 6.0
11.0 7.0
11.0 8.0
11.0 9.0
11.0 10.0
12.0 1.0
12.0 2.0
12.0 3.0
12.0 4.0
14.0 1.0
14.0 2.0
14.0 3.0
14.0 4.0
14.0 5.0
14.0 6.0
14.0 7.0
14.0 8.0
30.0 1.0
30.0 2.0
30.0 3.0
30.0 4.0
30.0 5.0
30.0 6.0
30.0 7.0
30.0 8.0
30.0 9.0
30.0 10.0
30.0 11.0
30.0 12.0
30.0 13.0
30.0 14.0
30.0 15.0
30.0 16.0
30.0 17.0
30.0 18.0
30.0 19.0
30.0 20.0
33.0 1.0
33.0 2.0
33.0 3.0
33.0 4.0
33.0 5.0
33.0 6.0
33.0 7.0
33.0 8.0
33.0 9.0
33.0 10.0
33.0 11.0
33.0 12.0
33.0 13.0
33.0 14.0
33.0 15.0
33.0 16.0
33.0 17.0
33.0 18.0
33.0 19.0
33.0 20.0
38.0 1.0
38.0 2.0
38.0 3.0
38.0 4.0
47.0 1.0
47.0 2.0
49.0 1.0
49.0 2.0
49.0 4.0
49.0 6.0
49.0 7.0
49.0 8.0
49.0 9.0
49.0 10.0
49.0 11.0
63.0 1.0
63.0 2.0
63.0 3.0
63.0 4.0
63.0 5.0
63.0 6.0
63.0 7.0
63.0 8.0
63.0 9.0
63.0 10.0
63.0 11.0
63.0 12.0
63.0 13.0
63.0 14.0
63.0 15.0
63.0 16.0
63.0 17.0
63.0 18.0
63.

302.0 9.0
302.0 10.0
302.0 11.0
302.0 12.0
302.0 13.0
302.0 14.0
302.0 15.0
302.0 16.0
302.0 17.0
302.0 18.0
302.0 19.0
302.0 20.0
312.0 1.0
312.0 2.0
312.0 3.0
312.0 4.0
312.0 5.0
312.0 6.0
312.0 7.0
312.0 8.0
312.0 9.0
312.0 10.0
312.0 11.0
312.0 12.0
312.0 13.0
312.0 14.0
312.0 15.0
312.0 16.0
312.0 17.0
315.0 1.0
315.0 2.0
315.0 3.0
315.0 4.0
315.0 5.0
315.0 6.0
315.0 7.0
315.0 8.0
318.0 1.0
318.0 2.0
318.0 3.0
318.0 4.0
318.0 5.0
318.0 6.0
318.0 7.0
318.0 8.0
318.0 11.0
319.0 1.0
319.0 3.0
319.0 4.0
319.0 5.0
319.0 6.0
319.0 7.0
320.0 1.0
320.0 2.0
320.0 3.0
320.0 4.0
320.0 5.0
320.0 6.0
320.0 7.0
321.0 1.0
321.0 2.0
321.0 3.0
321.0 4.0
321.0 5.0
321.0 6.0
321.0 7.0
321.0 8.0
322.0 1.0
322.0 2.0
322.0 3.0
322.0 4.0
322.0 5.0
322.0 6.0
322.0 7.0
322.0 8.0
322.0 9.0
322.0 10.0
322.0 11.0
322.0 12.0
322.0 13.0
322.0 14.0
322.0 15.0
322.0 16.0
325.0 1.0
325.0 2.0
325.0 3.0
325.0 4.0
325.0 5.0
325.0 6.0
325.0 7.0
325.0 8.0
325.0 9.0
325.0 10.0
325.0 11.0
325.0 12.0
329.0 1.0
329.0 2.0


643.0 14.0
643.0 15.0
643.0 16.0
643.0 17.0
643.0 18.0
643.0 19.0
643.0 20.0
647.0 1.0
647.0 2.0
647.0 3.0
647.0 4.0
647.0 5.0
647.0 6.0
647.0 7.0
647.0 8.0
647.0 9.0
647.0 10.0
647.0 11.0
647.0 12.0
647.0 13.0
647.0 14.0
647.0 15.0
647.0 16.0
647.0 17.0
653.0 1.0
653.0 2.0
653.0 3.0
653.0 4.0
653.0 5.0
660.0 1.0
660.0 2.0
660.0 3.0
660.0 4.0
660.0 5.0
660.0 6.0
660.0 7.0
660.0 8.0
660.0 9.0
660.0 10.0
660.0 11.0
660.0 12.0
660.0 13.0
660.0 14.0
660.0 15.0
660.0 16.0
660.0 17.0
660.0 18.0
660.0 19.0
660.0 20.0
662.0 1.0
662.0 2.0
662.0 3.0
662.0 4.0
662.0 5.0
662.0 6.0
662.0 7.0
662.0 8.0
662.0 9.0
664.0 1.0
664.0 2.0
664.0 3.0
664.0 4.0
664.0 5.0
664.0 6.0
664.0 7.0
664.0 8.0
664.0 9.0
664.0 10.0
671.0 1.0
671.0 2.0
671.0 3.0
671.0 4.0
671.0 5.0
671.0 6.0
671.0 7.0
671.0 8.0
671.0 9.0
674.0 1.0
674.0 4.0
685.0 1.0
685.0 2.0
685.0 3.0
685.0 4.0
686.0 1.0
686.0 2.0
686.0 3.0
686.0 4.0
686.0 5.0
686.0 6.0
686.0 7.0
686.0 8.0
686.0 9.0
686.0 10.0
686.0 11.0
686.0 12.0
686.0 13.0
686.0 14.

957.0 19.0
957.0 20.0
973.0 1.0
973.0 2.0
973.0 3.0
973.0 4.0
973.0 5.0
973.0 6.0
973.0 7.0
973.0 8.0
973.0 9.0
973.0 12.0
982.0 1.0
982.0 2.0
982.0 3.0
982.0 4.0
982.0 5.0
982.0 6.0
982.0 7.0
982.0 8.0
982.0 9.0
985.0 1.0
985.0 2.0
985.0 3.0
985.0 4.0
985.0 5.0
985.0 6.0
991.0 1.0
991.0 2.0
991.0 3.0
991.0 4.0
991.0 5.0
991.0 6.0
991.0 7.0
991.0 8.0
991.0 9.0
991.0 10.0
991.0 11.0
991.0 12.0
991.0 13.0
991.0 14.0
991.0 15.0
991.0 16.0
991.0 17.0
991.0 19.0
993.0 1.0
993.0 2.0
993.0 3.0
993.0 4.0
993.0 5.0
993.0 6.0
993.0 7.0
993.0 8.0
993.0 9.0
993.0 10.0
993.0 11.0
993.0 12.0
994.0 1.0
994.0 2.0
994.0 3.0
994.0 4.0
994.0 5.0
994.0 6.0
994.0 7.0
1004.0 1.0
1004.0 2.0
1004.0 3.0
1004.0 4.0
1004.0 5.0
1004.0 6.0
1004.0 7.0
1004.0 8.0
1005.0 1.0
1005.0 2.0
1005.0 3.0
1005.0 4.0
1005.0 5.0
1005.0 6.0
1005.0 7.0
1005.0 8.0
1005.0 9.0
1005.0 10.0
1005.0 11.0
1005.0 12.0
1005.0 13.0
1005.0 14.0
1005.0 15.0
1005.0 16.0
1005.0 17.0
1005.0 18.0
1005.0 19.0
1005.0 20.0
1006.0 1.0
1006.0 3.0
1006

1315.0 4.0
1315.0 5.0
1315.0 6.0
1317.0 1.0
1323.0 1.0
1323.0 2.0
1323.0 3.0
1323.0 4.0
1323.0 5.0
1323.0 6.0
1323.0 7.0
1323.0 8.0
1323.0 9.0
1323.0 10.0
1323.0 11.0
1323.0 12.0
1323.0 13.0
1323.0 14.0
1323.0 15.0
1323.0 16.0
1323.0 17.0
1323.0 18.0
1323.0 19.0
1323.0 20.0
1342.0 1.0
1342.0 2.0
1342.0 3.0
1342.0 4.0
1342.0 5.0
1342.0 6.0
1342.0 7.0
1342.0 8.0
1342.0 9.0
1342.0 11.0
1342.0 12.0
1342.0 13.0
1342.0 14.0
1342.0 15.0
1342.0 16.0
1342.0 17.0
1342.0 18.0
1342.0 19.0
1342.0 20.0
1358.0 1.0
1358.0 3.0
1358.0 4.0
1358.0 5.0
1358.0 6.0
1358.0 7.0
1358.0 8.0
1358.0 9.0
1358.0 10.0
1358.0 11.0
1358.0 12.0
1358.0 13.0
1358.0 14.0
1358.0 15.0
1358.0 16.0
1358.0 17.0
1358.0 18.0
1358.0 19.0
1359.0 1.0
1359.0 2.0
1359.0 3.0
1359.0 4.0
1359.0 5.0
1359.0 6.0
1360.0 1.0
1360.0 2.0
1360.0 3.0
1360.0 4.0
1360.0 5.0
1360.0 6.0
1360.0 7.0
1360.0 8.0
1360.0 9.0
1360.0 10.0
1360.0 11.0
1360.0 12.0
1360.0 13.0
1360.0 14.0
1360.0 15.0
1360.0 16.0
1360.0 17.0
1360.0 18.0
1360.0 19.0
1360.0 20.0
1

...

98512.0 8.0
98514.0 1.0
98514.0 2.0
98514.0 3.0
98514.0 4.0
98514.0 5.0
98514.0 6.0
98514.0 7.0
98514.0 8.0
98514.0 9.0
98514.0 10.0
98514.0 11.0
98514.0 12.0
98514.0 13.0
98514.0 14.0
98514.0 15.0
98514.0 16.0
98514.0 17.0
98514.0 18.0
98514.0 19.0
98514.0 20.0
98516.0 1.0
98516.0 2.0
98516.0 3.0
98516.0 4.0
98516.0 5.0
98516.0 6.0
98523.0 1.0
98523.0 3.0
98525.0 1.0
98525.0 2.0
98525.0 3.0
98525.0 4.0
98525.0 5.0
98525.0 6.0
98525.0 7.0
98525.0 8.0
98525.0 9.0
98525.0 10.0
98525.0 11.0
98525.0 12.0
98525.0 13.0
98525.0 14.0
98525.0 15.0
98525.0 16.0
98525.0 17.0
98525.0 20.0
98526.0 1.0
98526.0 2.0
98526.0 3.0
98526.0 5.0
98526.0 6.0
98526.0 7.0
98527.0 1.0
98527.0 2.0
98527.0 3.0
98527.0 4.0
98527.0 5.0
98530.0 1.0
98530.0 2.0
98530.0 3.0
98530.0 4.0
98530.0 5.0
98530.0 6.0
98530.0 7.0
98530.0 8.0
98530.0 9.0
98530.0 10.0
98530.0 11.0
98530.0 12.0
98530.0 13.0
98530.0 14.0
98530.0 15.0
98530.0 16.0
98530.0 17.0
98530.0 20.0
98533.0 1.0
98533.0 2.0
98533.0 3.0
98533.0 4.0
98533.0 5.0

98838.0 3.0
98838.0 4.0
98838.0 5.0
98838.0 6.0
98838.0 7.0
98838.0 8.0
98838.0 9.0
98838.0 10.0
98842.0 1.0
98842.0 2.0
98842.0 3.0
98842.0 4.0
98842.0 5.0
98847.0 1.0
98847.0 2.0
98847.0 3.0
98847.0 4.0
98847.0 5.0
98847.0 6.0
98847.0 7.0
98847.0 8.0
98847.0 12.0
98857.0 1.0
98857.0 3.0
98857.0 4.0
98857.0 5.0
98857.0 6.0
98857.0 7.0
98857.0 8.0
98857.0 9.0
98857.0 10.0
98857.0 11.0
98859.0 1.0
98859.0 2.0
98859.0 3.0
98859.0 4.0
98859.0 5.0
98859.0 6.0
98859.0 7.0
98859.0 8.0
98859.0 9.0
98864.0 1.0
98864.0 2.0
98864.0 3.0
98864.0 4.0
98864.0 5.0
98864.0 6.0
98876.0 1.0
98876.0 2.0
98876.0 3.0
98876.0 4.0
98876.0 5.0
98876.0 6.0
98876.0 7.0
98876.0 8.0
98880.0 1.0
98880.0 2.0
98880.0 3.0
98880.0 4.0
98880.0 5.0
98880.0 6.0
98880.0 7.0
98880.0 8.0
98880.0 9.0
98880.0 10.0
98880.0 11.0
98880.0 15.0
98890.0 1.0
98890.0 2.0
98890.0 3.0
98890.0 4.0
98890.0 5.0
98890.0 6.0
98890.0 7.0
98890.0 8.0
98890.0 9.0
98890.0 10.0
98890.0 11.0
98890.0 12.0
98890.0 13.0
98890.0 14.0
98890.0 15.0
988

99167.0 1.0
99167.0 3.0
99170.0 1.0
99170.0 2.0
99170.0 3.0
99170.0 4.0
99170.0 5.0
99170.0 6.0
99173.0 1.0
99173.0 2.0
99173.0 3.0
99173.0 4.0
99173.0 5.0
99173.0 6.0
99173.0 7.0
99173.0 8.0
99173.0 9.0
99175.0 1.0
99175.0 2.0
99175.0 3.0
99175.0 4.0
99175.0 5.0
99175.0 6.0
99175.0 7.0
99175.0 8.0
99175.0 9.0
99175.0 10.0
99175.0 12.0
99186.0 1.0
99186.0 2.0
99186.0 3.0
99186.0 4.0
99186.0 5.0
99186.0 6.0
99186.0 7.0
99186.0 9.0
99187.0 1.0
99187.0 2.0
99187.0 3.0
99187.0 4.0
99187.0 5.0
99187.0 6.0
99187.0 7.0
99187.0 8.0
99190.0 1.0
99190.0 2.0
99190.0 3.0
99190.0 4.0
99190.0 5.0
99190.0 6.0
99190.0 7.0
99190.0 8.0
99190.0 9.0
99190.0 11.0
99196.0 1.0
99196.0 2.0
99196.0 3.0
99196.0 4.0
99196.0 5.0
99196.0 6.0
99196.0 7.0
99196.0 8.0
99196.0 9.0
99196.0 10.0
99196.0 11.0
99196.0 12.0
99196.0 13.0
99196.0 14.0
99196.0 15.0
99199.0 1.0
99206.0 1.0
99206.0 2.0
99206.0 3.0
99206.0 4.0
99206.0 5.0
99206.0 6.0
99206.0 7.0
99206.0 8.0
99206.0 9.0
99206.0 10.0
99206.0 11.0
99206.0 12.0
9920

99490.0 6.0
99499.0 1.0
99499.0 2.0
99499.0 3.0
99499.0 4.0
99499.0 5.0
99499.0 6.0
99500.0 1.0
99500.0 2.0
99500.0 4.0
99500.0 6.0
99500.0 7.0
99502.0 1.0
99502.0 2.0
99502.0 3.0
99502.0 4.0
99502.0 5.0
99502.0 9.0
99509.0 1.0
99509.0 2.0
99509.0 3.0
99509.0 4.0
99509.0 5.0
99509.0 6.0
99509.0 7.0
99509.0 8.0
99509.0 9.0
99509.0 10.0
99509.0 11.0
99509.0 12.0
99509.0 13.0
99509.0 14.0
99509.0 15.0
99509.0 16.0
99509.0 17.0
99509.0 19.0
99516.0 1.0
99516.0 2.0
99516.0 3.0
99516.0 4.0
99516.0 5.0
99516.0 6.0
99516.0 7.0
99516.0 8.0
99516.0 9.0
99516.0 10.0
99516.0 11.0
99516.0 12.0
99516.0 13.0
99516.0 14.0
99516.0 15.0
99516.0 16.0
99516.0 17.0
99516.0 18.0
99516.0 19.0
99516.0 20.0
99518.0 1.0
99518.0 2.0
99518.0 3.0
99518.0 4.0
99518.0 5.0
99518.0 6.0
99518.0 7.0
99518.0 8.0
99518.0 9.0
99518.0 10.0
99518.0 11.0
99518.0 12.0
99518.0 13.0
99518.0 14.0
99518.0 15.0
99520.0 1.0
99520.0 2.0
99520.0 3.0
99520.0 4.0
99520.0 5.0
99520.0 6.0
99520.0 7.0
99520.0 8.0
99520.0 9.0
99526.0 1.0
99

99846.0 18.0
99846.0 19.0
99852.0 1.0
99852.0 2.0
99852.0 3.0
99852.0 4.0
99852.0 5.0
99852.0 6.0
99852.0 7.0
99852.0 8.0
99852.0 9.0
99852.0 10.0
99852.0 11.0
99852.0 12.0
99852.0 13.0
99852.0 14.0
99852.0 15.0
99852.0 16.0
99852.0 17.0
99852.0 18.0
99852.0 19.0
99852.0 20.0
99855.0 1.0
99855.0 2.0
99855.0 3.0
99855.0 4.0
99855.0 5.0
99855.0 6.0
99855.0 7.0
99855.0 8.0
99855.0 9.0
99855.0 10.0
99855.0 11.0
99855.0 12.0
99855.0 13.0
99855.0 14.0
99855.0 15.0
99855.0 16.0
99855.0 17.0
99855.0 18.0
99855.0 19.0
99855.0 20.0
99856.0 1.0
99856.0 5.0
99856.0 6.0
99856.0 7.0
99856.0 8.0
99856.0 9.0
99856.0 10.0
99856.0 11.0
99856.0 12.0
99858.0 1.0
99858.0 2.0
99858.0 3.0
99858.0 4.0
99858.0 5.0
99858.0 6.0
99858.0 7.0
99858.0 8.0
99858.0 9.0
99858.0 10.0
99862.0 1.0
99862.0 2.0
99862.0 6.0
99863.0 1.0
99863.0 2.0
99863.0 3.0
99863.0 4.0
99863.0 5.0
99863.0 6.0
99863.0 7.0
99863.0 8.0
99863.0 9.0
99863.0 10.0
99863.0 11.0
99863.0 12.0
99863.0 13.0
99863.0 14.0
99863.0 15.0
99863.0 16.0
99863

In [160]:
# If a patient has Sepsis, they should remain flagged as such, even if they get better
patientdata = sepsisFound(patientdata, "qSOFAFlag")

Finished


In [163]:
patientdata = sepsisFound(patientdata, "SOFAFlag")

Finished


In [84]:
patientdata.apply(sepsisFound, axis=1, framedata = patientdata, option="SOFAFlag")

0         None
1         None
2         None
3         None
4         None
          ... 
238325    None
238326    None
238327    None
238328    None
238329    None
Length: 238330, dtype: object

In [164]:
patientdata.head()

bloc  icustayid   charttime  gender           age  elixhauser  \
0     1          3  7245399600       0  17639.826435           0   
1     2          3  7245414000       0  17639.826435           0   
2     3          3  7245428400       0  17639.826435           0   
3     4          3  7245442800       0  17639.826435           0   
4     5          3  7245457200       0  17639.826435           0   

   re_admission  died_in_hosp  died_within_48h_of_out_time  mortality_90d  \
0             0             0                            0              1   
1             0             0                            0              1   
2             0             0                            0              1   
3             0             0                            0              1   
4             0             0                            0              1   

   ...  input_total  input_4hourly  output_total  output_4hourly  \
0  ...       6297.0           30.0       10987.0           580.0   
1  ...       6347.0           50.0       11562.0           575.0   
2  ...       6397.0           50.0       12412.0           850.0   
3  ...       6447.0           50.0       13062.0           650.0   
4  ...       6477.0           30.0       13532.0           470.0   

   cumulated_balance  SOFA  SIRS  qSOFA  qSOFAFlag  SOFAFlag  
0            -4690.0     3     1      2          1         0  
1            -5215.0     7     2      1          1         1  
2            -6015.0     7     2      1          1         1  
3            -6615.0     7     1      1          1         1  
4            -7055.0     6     3      2          1         1  

[5 rows x 62 columns]

In [165]:
patientdata.to_csv("G:/MIMIC-ALL/MIMIC-PATIENTS/patient_data_modified.csv")